## Effects of Cosmological Parameters on Mira Titan Emulator HMF

In [237]:
import numpy as np
import MiraTitanHMFemulator
import bokeh
from bokeh.io import output_notebook, show, curdoc
from bokeh.plotting import figure
from bokeh.layouts import row, column
from bokeh.models import ColumnDataSource, HoverTool, Slider, CustomJS
from bokeh.palettes import Spectral, d3, RdYlGn
output_notebook()

Loading BokehJS ...

### Borg Cube Parameters

In [238]:
fid_cosmology = {
        "Ommh2": 0.2648*0.71*0.71,
        "Ombh2": 0.0448*0.71*0.71,
        "Omnuh2": 0,
        "n_s": 0.963,
        "h": 0.71,
        "sigma_8": 0.8,
        "w_0": -1,
        "w_a": 0,
        "w_b": 1
    }

In [239]:
param_names = {'Ommh2': "Omega_m h^2",
               'Ombh2': "Omega_b h^2", 
               'Omnuh2': "Omega_nu h^2", 
               'n_s': "n_s", 
               'h': "h", 
               'sigma_8': "sigma_8", 
               'w_0': "w_0", 
               'w_b': "w_b"}

 ### Emulator Parameter Ranges

In [240]:
param_limits = {
    'Ommh2': (.12, .155),
    'Ombh2': (.0215, .0235),
    'Omnuh2': (0, .01),
    'n_s': (.85, 1.05),
    'h': (.55, .85),
    'sigma_8': (.7, .9),
    'w_0': (-1.3, -.7),
    'w_b': (.3, 1.3),
}

In [241]:
z_arr = np.linspace(0., 2, 21)
m_arr = np.logspace(13, 15, 1000)
nsteps = 11
emu = MiraTitanHMFemulator.Emulator()
fid_dNdlnM = emu.predict(fid_cosmology, z_arr, m_arr, get_errors=False)[0]

In [242]:
param_ranges = {}
for param in param_names.keys():
    param_ranges[param] = np.linspace(param_limits[param][0], param_limits[param][1], nsteps)

In [243]:
curdoc().theme = "night_sky"

HMF_plots = {0: [], 1: []}
ratio_plots = {0: [], 1: []}
for i, param in enumerate(param_names.keys()):
    p_0 = figure(plot_height=250, plot_width=400, title=f"{param_names[param]}, Redshift = 0", 
                 x_axis_type="log", y_axis_type="log", tools="pan,box_zoom,wheel_zoom,reset")
    p2_0 = figure(plot_height=250, plot_width=400, title=f"{param_names[param]}, Redshift = 0", 
                  x_axis_type="log", tools="pan,box_zoom,wheel_zoom,reset")
    
    p_1 = figure(plot_height=250, plot_width=400, title=f"{param_names[param]}, Redshift = 1", 
                 x_axis_type="log", y_axis_type="log", tools="pan,box_zoom,wheel_zoom,reset")
    p2_1 = figure(plot_height=250, plot_width=400, title=f"{param_names[param]}, Redshift = 1", 
                  x_axis_type="log", tools="pan,box_zoom,wheel_zoom,reset")

    for par_val, col in zip(param_ranges[param], RdYlGn[11]):
        cosmology = fid_cosmology.copy()
        cosmology[param] = par_val
        if param == "w_b":
            cosmology["w_a"] = -(par_val**4 + cosmology["w_0"])
        
        dNdlnM = emu.predict(cosmology, z_arr, m_arr, get_errors=False)[0]
        
        
        p_0.line(m_arr, dNdlnM[0], color=col, legend_label=f"{par_val:.4f}", line_width=1.5)
        p2_0.line(m_arr, dNdlnM[0]/fid_dNdlnM[0], color=col, line_width=1.5)
        
        p_1.line(m_arr, dNdlnM[10], color=col, legend_label=f"{par_val:.4f}", line_width=1.5)
        p2_1.line(m_arr, dNdlnM[10]/fid_dNdlnM[10], color=col, line_width=1.5)
    
    p_0.line(m_arr, fid_dNdlnM[0], color="white", legend_label="Borg Cube", line_width=1.8)
    p2_0.line(m_arr, 1, color="white", line_width=1.8)
    
    p_1.line(m_arr, fid_dNdlnM[10], color="white", legend_label="Borg Cube", line_width=1.8)
    p2_1.line(m_arr, 1, color="white", line_width=1.8)
    
    p_0.xaxis.axis_label = r"$$\color{white} \text{Mass}\ M_{200c},\ h^{-1}M_{\odot}$$"
    p_0.yaxis.axis_label = r"$$\color{white} dN/d\ln{M},\ (h/\mathrm{Mpc}^3)$$"
    p2_0.xaxis.axis_label = r"$$\color{white} \text{Mass}\ M_{200c},\ h^{-1}M_{\odot}$$"
    p2_0.yaxis.axis_label = r"$$\color{white} \frac{dN/d\ln{M}}{dN/d\ln{M}|_{\text{BC}}}$$"
    
    p_0.xaxis.axis_label_text_font_size = "12px"
    p_0.yaxis.axis_label_text_font_size = "12px"
    p2_0.xaxis.axis_label_text_font_size = "12px"
    p2_0.yaxis.axis_label_text_font_size = "12px"
    
    
    p_1.xaxis.axis_label = r"$$\color{white} \text{Mass}\ M_{200c},\ h^{-1}M_{\odot}$$"
    p_1.yaxis.axis_label = r"$$\color{white} dN/d\ln{M},\ (h/\mathrm{Mpc}^3)$$"
    p2_1.xaxis.axis_label = r"$$\color{white} \text{Mass}\ M_{200c},\ h^{-1}M_{\odot}$$"
    p2_1.yaxis.axis_label = r"$$\color{white} \frac{dN/d\ln{M}}{dN/d\ln{M}|_{\text{BC}}}$$"
    
    p_1.xaxis.axis_label_text_font_size = "12px"
    p_1.yaxis.axis_label_text_font_size = "12px"
    p2_1.xaxis.axis_label_text_font_size = "12px"
    p2_1.yaxis.axis_label_text_font_size = "12px"
    
    for item in p_0.legend.items[1:-2]:
        item.visible = False
        
    for item in p_1.legend.items[1:-2]:
        item.visible = False

    p_0.legend.location = "bottom_left"
    p_1.legend.location = "bottom_left"
    
    HMF_plots[0].append(p_0)
    ratio_plots[0].append(p2_0)
    ratio_plots[0][i].x_range = HMF_plots[0][i].x_range
    
    HMF_plots[1].append(p_1)
    ratio_plots[1].append(p2_1)
    ratio_plots[1][i].x_range = HMF_plots[1][i].x_range

### $$\Omega_m h^2$$

In [244]:
show(column(row(HMF_plots[0][0], ratio_plots[0][0]), row(HMF_plots[1][0], ratio_plots[1][0])))

### $$\Omega_b h^2$$

In [245]:
show(column(row(HMF_plots[0][1], ratio_plots[0][1]), row(HMF_plots[1][1], ratio_plots[1][1])))

### $$\Omega_{\nu} h^2$$

In [246]:
show(column(row(HMF_plots[0][2], ratio_plots[0][2]), row(HMF_plots[1][2], ratio_plots[1][2])))

### $$n_s$$

In [247]:
show(column(row(HMF_plots[0][3], ratio_plots[0][3]), row(HMF_plots[1][3], ratio_plots[1][3])))

### $$h$$

In [248]:
show(column(row(HMF_plots[0][4], ratio_plots[0][4]), row(HMF_plots[1][4], ratio_plots[1][4])))

### $$\sigma_8$$

In [249]:
show(column(row(HMF_plots[0][5], ratio_plots[0][5]), row(HMF_plots[1][5], ratio_plots[1][5])))

### $$w_0$$

In [250]:
show(column(row(HMF_plots[0][6], ratio_plots[0][6]), row(HMF_plots[1][6], ratio_plots[1][6])))

### $$w_b$$

In [251]:
show(column(row(HMF_plots[0][7], ratio_plots[0][7]), row(HMF_plots[1][7], ratio_plots[1][7])))